In [1]:
!pip install haversine

In [125]:
import pandas as pd
import numpy as np
import pickle
from sklearn.metrics import f1_score
from sklearn.model_selection import train_test_split
from haversine import haversine
from sklearn.cluster import KMeans
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV
from sklearn.metrics import accuracy_score,classification_report
#from mdlp.discretization import MDLP

In [72]:
bookings_original = pd.read_csv("data/raw/booking_log.csv")
participants_original = pd.read_csv("data/raw/participant_log.csv")
test = pd.read_csv("data/raw/test_data.csv")

In [6]:
test.shape

(100000, 10)

# EDA

In [73]:
bookings_original.head(5),bookings_original.shape

(                  event_timestamp      order_id booking_status   customer_id  \
 0     2015-05-12 05:25:23.904 UTC  102254181112        CREATED  715281995014   
 1      2015-05-12 05:25:24.67 UTC  102254181112   DRIVER_FOUND  715281995014   
 2  2015-05-12 05:55:10.496544 UTC  102254181112      COMPLETED  715281995014   
 3     2015-05-12 05:29:37.305 UTC  105520285203        CREATED  957980952237   
 4     2015-05-12 05:29:38.214 UTC  105520285203   DRIVER_FOUND  957980952237   
 
       driver_id  trip_distance  pickup_latitude  pickup_longitude  
 0           NaN            2.0        -2.998461        104.788077  
 1  2.211727e+11            2.0        -2.998461        104.788077  
 2  2.211727e+11            2.0        -2.998461        104.788077  
 3           NaN            2.0        -2.970621        104.756226  
 4  5.276724e+11            2.0        -2.970621        104.756226  ,
 (699212, 8))

In [76]:
bookings = bookings_original.drop(['event_timestamp','booking_status','driver_id'],axis=1)

In [9]:
unique_columns = [
        "order_id",
        "trip_distance",
        "pickup_latitude",
        "pickup_longitude",
    ]
bookings = bookings.drop_duplicates(subset=unique_columns)

In [10]:
participants = participants_original.drop_duplicates()
participants.head(5),participants.shape

(               event_timestamp     driver_id participant_status      order_id  \
 0  2015-05-18 11:45:19.519 UTC  110283102582            CREATED  938125906616   
 1    2015-05-18 11:45:29.8 UTC  110283102582           ACCEPTED  938125906616   
 2  2015-05-11 10:35:57.021 UTC  126346998414            CREATED  992080359113   
 3  2015-05-11 10:36:01.148 UTC  126346998414           ACCEPTED  992080359113   
 4  2015-05-16 12:34:20.044 UTC  199325048812           ACCEPTED  797723880713   
 
    experiment_key  driver_latitude  driver_longitude  driver_gps_accuracy  
 0    309579604593        -2.981389        104.761898                  2.0  
 1    309579604593        -2.981389        104.761898                  2.0  
 2    941995970460        -2.966915        104.748040                  2.0  
 3    941995970460        -2.966915        104.748040                  2.0  
 4    197604093364        -3.014740        104.694647                  2.0  ,
 (400104, 8))

In [88]:
pd.DataFrame(participants.groupby(["order_id"])["driver_id"].nunique())["driver_id"].value_counts()

1     162619
2      14260
3       2152
4        459
5        113
6         58
7         22
8         10
9          2
13         1
10         1
Name: driver_id, dtype: int64

In [91]:
bookings["order_id"].nunique()

185867

In [92]:
#8133 order_ids have 0 drivers because these orders were only created and no driver was assigned to them, rest orders driver was assigned.
#8133+177734=185867 (total order_ids)
pd.DataFrame(bookings_original.groupby(["order_id"])["driver_id"].nunique())["driver_id"].value_counts()

1    177734
0      8133
Name: driver_id, dtype: int64

In [79]:
test.groupby("order_id")["driver_id"].nunique()

order_id
100042151807    10
100081753505    10
100161922318    10
100241210016    10
100257841517    10
                ..
898811959012    10
898830876614    10
898964332814    10
899096511800    10
899231424316    10
Name: driver_id, Length: 10000, dtype: int64

In [11]:
test.head(5),test.shape

(               event_timestamp      order_id   customer_id  trip_distance  \
 0  2015-05-20 05:31:12.822 UTC  300202530411  470195505600            2.0   
 1  2015-05-20 05:31:12.822 UTC  300202530411  470195505600            2.0   
 2  2015-05-20 05:31:12.822 UTC  300202530411  470195505600            2.0   
 3  2015-05-20 05:31:12.822 UTC  300202530411  470195505600            2.0   
 4  2015-05-20 05:31:12.822 UTC  300202530411  470195505600            2.0   
 
    pickup_latitude  pickup_longitude     driver_id  driver_latitude  \
 0        -2.977965         104.77559  578486386000        -2.979892   
 1        -2.977965         104.77559  919898718450        -2.979352   
 2        -2.977965         104.77559  566354734208        -2.978990   
 3        -2.977965         104.77559  996326998494        -2.979434   
 4        -2.977965         104.77559  110774820109        -2.979365   
 
    driver_longitude  driver_gps_accuracy  
 0        104.775853              104.100  
 1      

In [12]:
dataset = pd.merge(participants,bookings, on = "order_id", how="left")

In [13]:
#19May 2015 is missing in participants_log but is present in bookings_log, bcoz merge is done on participants, dataset does not have this date
dataset.event_timestamp.min(),dataset.event_timestamp.max(),test.event_timestamp.min(),test.event_timestamp.max(),participants.event_timestamp.max()

('2015-05-10 00:00:11.845 UTC',
 '2015-05-18 23:59:59.632 UTC',
 '2015-05-20 00:00:18.427 UTC',
 '2015-05-20 23:59:58.789 UTC',
 '2015-05-18 23:59:59.632 UTC')

In [14]:
dataset.drop(['experiment_key'],inplace=True,axis=1)
dataset.shape

(400104, 11)

In [15]:
#This shows that maximum 174/2 requests lie with 1 driver in this dataset as largely each driver with request will have 2 entries,
# one at time of creation and other at time of response
dataset.driver_id.value_counts()

621987433025    174
622447347300    172
271936096806    166
178632046874    163
766627766512    163
               ... 
902095281838      1
917939363137      1
732388817640      1
709961499772      1
204107384010      1
Name: driver_id, Length: 14913, dtype: int64

In [16]:
dataset.head(5)

event_timestamp     driver_id participant_status      order_id  \
0  2015-05-18 11:45:19.519 UTC  110283102582            CREATED  938125906616   
1    2015-05-18 11:45:29.8 UTC  110283102582           ACCEPTED  938125906616   
2  2015-05-11 10:35:57.021 UTC  126346998414            CREATED  992080359113   
3  2015-05-11 10:36:01.148 UTC  126346998414           ACCEPTED  992080359113   
4  2015-05-16 12:34:20.044 UTC  199325048812           ACCEPTED  797723880713   

   driver_latitude  driver_longitude  driver_gps_accuracy   customer_id  \
0        -2.981389        104.761898                  2.0  786955815516   
1        -2.981389        104.761898                  2.0  786955815516   
2        -2.966915        104.748040                  2.0  758692050609   
3        -2.966915        104.748040                  2.0  758692050609   
4        -3.014740        104.694647                  2.0  967731380169   

   trip_distance  pickup_latitude  pickup_longitude  
0          5.601        -2.980337        104.761200  
1          5.601        -2.980337        104.761200  
2          1.744        -2.968359        104.749344  
3          1.744        -2.968359        104.749344  
4          2.505        -3.013223        104.700030

In [17]:
#This code finds those order_ID and driver_id pairs for which only CREATED status row is present and there is no info about driver's response.
#Also it helps us to know if this behaviour is driver dependent. .
dataset.groupby(["order_id","driver_id"]).filter(lambda x: len(x)==1)["driver_id"].value_counts()

705573313466    7
457765057674    4
238210291329    4
381538151896    4
174566916689    4
               ..
189731800340    1
368151360724    1
699542607016    1
347825505488    1
475534069815    1
Name: driver_id, Length: 1000, dtype: int64

In [18]:
#This checks how many requests did the above driver "705573313466" got in order to know the ratio of rides for which info is
#absent and 43/2 i.e out od 21 rides information for 7 rides is missing. Info below shows that maybe this driver is faulty or  
#Maybe that data is missing and hence we can remove those rows
dataset["driver_id"].value_counts()[705573313466]

43

In [19]:
#Creating a column called "driver response time" by subtracting the timestamp in the two rows with 
#respective CREATED and "ACCEPTED/REJECTED/IGNORED" value.
dataset_featured = dataset.groupby(["order_id","driver_id"]).filter(lambda x: len(x)>1)

In [95]:
dataset_featured.shape

(398970, 11)

In [98]:
pd.DataFrame(dataset_featured.groupby(["order_id"])["driver_id"].nunique())["driver_id"].value_counts()

1     161884
2      14172
3       2107
4        447
5        110
6         55
7         21
8         10
9          2
13         1
10         1
Name: driver_id, dtype: int64

# Feature Engineering

In [20]:
def response_time(order):
    order = pd.DataFrame(order)
    if order.iloc[0]["participant_status"] == "CREATED":
        order["driver_response_time"] = (order.iloc[1]["event_timestamp"] - order.iloc[0]["event_timestamp"]).total_seconds()
        print(type(order.iloc[0]["driver_response_time"]))
    else:
        order["driver_response_time"] = (order.iloc[0]["event_timestamp"] - order.iloc[1]["event_timestamp"]).total_seconds()
    return order

In [21]:
def get_cartesian(lat=None,lon=None):
    lat, lon = np.deg2rad(lat), np.deg2rad(lon)
    R = 6371 # radius of the earth
    x = R * np.cos(lat) * np.cos(lon)
    y = R * np.cos(lat) * np.sin(lon)
    z = R *np.sin(lat)
    return [x,y,z]

In [22]:
# #Find best K using elbow method. Result : K=25
# K = range(5, 50)
# inertias = [] 
# for k in K:
#     kmeanModel = KMeans(n_clusters=k).fit(df_cord_driver_cartesian)
#     inertias.append(kmeanModel.inertia_)

In [23]:
#If we were given personal info about the driver we could have had more feature columns describing the driver
def transform_train_val_test(df,train_or_test):
    df["event_timestamp"]=df["event_timestamp"].apply(lambda x: pd.to_datetime(x))
    #print(df["event_timestamp"])
    #df["date"] = df.event_timestamp.dt.date
    df["dayofweek"] = df.event_timestamp.dt.dayofweek
    df["hourofday"] = df.event_timestamp.dt.hour
    if train_or_test in ["train","val"]:
        df['participant_status'] = df['participant_status'].astype(str)
        df = df.groupby(["order_id","driver_id"]).apply(response_time)
        df = df[~(df["participant_status"].str.contains("CREATED"))]#As this info has been captured in "driver_response_time"
        df["participant_status"] = df["participant_status"].apply(lambda x: 1 if x=="ACCEPTED" else 0)
        driver_wise_response_time = pd.DataFrame(df.groupby(["driver_id"])["driver_response_time"].mean())
        driver_wise_response_time.to_csv("driver_wise_response_time.csv")
    if train_or_test == "test":
        driver_wise_response_time= pd.read_csv("driver_wise_response_time.csv")
        df = pd.merge(df,driver_wise_response_time, on="driver_id",how="left").fillna(driver_wise_response_time["driver_response_time"].mean())
#         transformer = MDLP(continuous_features=[True])
#         df['hourly_bins'] = transformer.fit_transform(np.array(df['hourofday']).reshape(-1, 1), df['participant_status'])
#         pickle.dump(transformer, open('transformer.pkl', 'wb'))
#     transformer = pickle.load(open("transformer.pkl", 'rb'))   
#     df['hourly_bins'] = transformer.transform(np.array(df['hourofday']).reshape(-1, 1), df['participant_status'])
    #df.groupby("hourofday")['is_accepted'].mean().plot , Plot shows that busy hours are between 5 and 15.
    df["is_busy_hour"] = df["hourofday"].apply(lambda x:  1 if x>=5 and x<=15 else 0)
    df["driver_distance"] = df.apply(lambda r: haversine((r["driver_latitude"], r["driver_longitude"]),
                            (r["pickup_latitude"], r["pickup_longitude"])),axis=1)
    df_cord_driver_cartesian = pd.DataFrame(df[["driver_latitude", "driver_longitude"]].apply(lambda x: get_cartesian(x["driver_latitude"],x["driver_longitude"]),axis=1).tolist())
    df_cord_customer_cartesian = pd.DataFrame(df[["pickup_latitude", "pickup_longitude"]].apply(lambda x: get_cartesian(x["pickup_latitude"],x["pickup_longitude"]),axis=1).tolist())    
    if train_or_test == "train":
        kmeanModel = KMeans(n_clusters=25).fit(df_cord_driver_cartesian)
        with open("kmeanModel.pkl", "wb") as f:
            pickle.dump(kmeanModel, f)
    kmeanModel = pickle.load(open("kmeanModel.pkl", 'rb'))
    df["driver_cluster_label"]= kmeanModel.predict(df_cord_driver_cartesian).tolist()
    df["customer_cluster_label"]= kmeanModel.predict(df_cord_customer_cartesian).tolist()
    df.drop(["event_timestamp","driver_latitude", "driver_longitude","pickup_latitude", "pickup_longitude","hourofday"],inplace=True, axis=1)
    return df

In [24]:
#Divide data into train and val after sorting on time so that while training we do not have future ride info
dataset_featured = dataset_featured.sort_values(by='event_timestamp',ascending=True)
dataset_featured_train, dataset_featured_val = dataset_featured.head(int(len(dataset_featured)*(80/100))),dataset_featured.tail(int(len(dataset_featured)*(20/100)))

In [25]:
transformed_train_data = transform_train_val_test(dataset_featured_train,"train")
transformed_val_data = transform_train_val_test(dataset_featured_val.sort_values(by='order_id',ascending=True),"val")
transformed_test_data = transform_train_val_test(test,"test")

<ipython-input-23-ca30c9b03584>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["event_timestamp"]=df["event_timestamp"].apply(lambda x: pd.to_datetime(x))
<ipython-input-23-ca30c9b03584>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["dayofweek"] = df.event_timestamp.dt.dayofweek
<ipython-input-23-ca30c9b03584>:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation:

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

...

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.float64'>
<class 'numpy.fl

In [99]:
transformed_train_data["participant_status"].value_counts()

1    144652
0     14936
Name: participant_status, dtype: int64

In [26]:
# transformed_train_data = transform_train_val_test(dataset_featured_train[:100],"train")
# transformed_val_data = transform_train_val_test(dataset_featured_val.sort_values(by='order_id',ascending=True)[:20],"val")
# transformed_test_data = transform_train_val_test(test[:30],"test")

In [27]:
transformed_train_data.columns,transformed_test_data.columns

(Index(['driver_id', 'participant_status', 'order_id', 'driver_gps_accuracy',
        'customer_id', 'trip_distance', 'dayofweek', 'driver_response_time',
        'is_busy_hour', 'driver_distance', 'driver_cluster_label',
        'customer_cluster_label'],
       dtype='object'),
 Index(['order_id', 'customer_id', 'trip_distance', 'driver_id',
        'driver_gps_accuracy', 'dayofweek', 'driver_response_time',
        'is_busy_hour', 'driver_distance', 'driver_cluster_label',
        'customer_cluster_label'],
       dtype='object'))

In [28]:
train_y = transformed_train_data["participant_status"]
train_x = transformed_train_data.drop(["participant_status","order_id","customer_id"],axis=1)
val_y = transformed_val_data["participant_status"]
val_x = transformed_val_data.drop(["participant_status","order_id","customer_id"],axis=1)
#test = transformed_test_data

In [110]:
!conda install imblearn


PackagesNotFoundError: The following packages are not available from current channels:

  - imblearn

Current channels:

  - https://repo.anaconda.com/pkgs/main/win-64
  - https://repo.anaconda.com/pkgs/main/noarch
  - https://repo.anaconda.com/pkgs/r/win-64
  - https://repo.anaconda.com/pkgs/r/noarch
  - https://repo.anaconda.com/pkgs/msys2/win-64
  - https://repo.anaconda.com/pkgs/msys2/noarch

To search for alternate channels that may provide the conda package you're
looking for, navigate to

    https://anaconda.org

and use the search bar at the top of the page.





Solving environment: ...working... failed with initial frozen solve. Retrying with flexible solve.
Solving environment: ...working... failed with initial frozen solve. Retrying with flexible solve.


In [113]:
#SMOTE
from imblearn.over_sampling import SMOTE
import numpy as np
sm = SMOTE(random_state=12)
x_train_res, y_train_res = sm.fit_resample(train_x, train_y)
print (train_y.value_counts())
np.bincount(y_train_res)

1    144652
0     14936
Name: participant_status, dtype: int64


array([144652, 144652], dtype=int64)

In [114]:
transformed_train_data.to_csv("data/processed/train_data_mahima.csv")
#transformed_test_data.to_csv("data/processed/test_data_mahima.csv")

In [115]:
val_y.shape,val_x.shape

((39897,), (39897, 9))

In [155]:
train_x.columns

Index(['driver_id', 'driver_gps_accuracy', 'trip_distance', 'dayofweek',
       'driver_response_time', 'is_busy_hour', 'driver_distance',
       'driver_cluster_label', 'customer_cluster_label'],
      dtype='object')

In [116]:
x_train_res.columns

Index(['driver_id', 'driver_gps_accuracy', 'trip_distance', 'dayofweek',
       'driver_response_time', 'is_busy_hour', 'driver_distance',
       'driver_cluster_label', 'customer_cluster_label'],
      dtype='object')

In [117]:
val_x.columns

Index(['driver_id', 'driver_gps_accuracy', 'trip_distance', 'dayofweek',
       'driver_response_time', 'is_busy_hour', 'driver_distance',
       'driver_cluster_label', 'customer_cluster_label'],
      dtype='object')

In [118]:
y_train_res.value_counts()

1    144652
0    144652
Name: participant_status, dtype: int64

I tried the following algorithms: Logistic Regression, K Nearest Neighbors, Gradient Boosting Classifier, Decision Tree, Random Forest, Neural Net. Below are the results and explanation of top performing machine learning algorithms.

In [160]:
#This gives the rows added by SMOTE
df_all = x_train_res.merge(train_x.drop_duplicates(),how='left', indicator=True)
df_all.loc[df_all['_merge'] == 'left_only']

driver_id  driver_gps_accuracy  trip_distance  dayofweek  \
159588  991055096899             4.356323       8.526473          1   
159589  439227850321             3.082150       6.046809          2   
159590  248965823752            16.623394       7.973436          2   
159591  443933965322            12.575203       7.063159          3   
159592  793288794356             4.557807       5.802477          5   
...              ...                  ...            ...        ...   
289299  217151633705             5.489608       1.306766          2   
289300  309464742400           948.241670       5.478339          5   
289301  906838027027            10.958938       4.339094          1   
289302  660926051479            15.005495       1.903720          4   
289303  382898281940             6.649265       3.732792          2   

        driver_response_time  is_busy_hour  driver_distance  \
159588             15.026875             0         0.093673   
159589             15.023544             1         0.279660   
159590             15.016623             0         0.035480   
159591             15.017408             1         0.374738   
159592             15.036253             0         0.607187   
...                      ...           ...              ...   
289299             15.014242             0         0.195945   
289300             15.022700             0         0.694144   
289301             15.017316             0         0.095984   
289302             15.019180             1         0.038072   
289303             15.014000             1         0.196058   

        driver_cluster_label  customer_cluster_label     _merge  
159588                    19                      19  left_only  
159589                     2                      16  left_only  
159590                     2                       2  left_only  
159591                    18                      18  left_only  
159592                     0                       0  left_only  
...                      ...                     ...        ...  
289299                     5                       5  left_only  
289300                     6                       6  left_only  
289301                    13                      13  left_only  
289302                    11                      11  left_only  
289303                     7                       7  left_only  

[129716 rows x 10 columns]

# Modelling

LR or SVM as we are dealing with 2 class problem. SVM works well with unstructured and semi-structured data like text and images while logistic regression works with already identified independent variables. 

In [127]:
from sklearn.ensemble import RandomForestClassifier
model = RandomForestClassifier(n_estimators=100)
model.fit(x_train_res , y_train_res)
y_pred = model.predict(val_x)
target_names = ['Accept', 'Not_Accept']
print(classification_report(val_y, y_pred))#,target_names=target_names)

              precision    recall  f1-score   support

           0       0.91      0.93      0.92      3846
           1       0.99      0.99      0.99     36051

    accuracy                           0.98     39897
   macro avg       0.95      0.96      0.95     39897
weighted avg       0.98      0.98      0.98     39897



In [128]:
from sklearn.ensemble import GradientBoostingClassifier
model_GB = GradientBoostingClassifier(n_estimators=100)
model_GB.fit(x_train_res , y_train_res)
y_pred = model_GB.predict(val_x)
target_names = ['Accept', 'Not_Accept']
print(classification_report(val_y, y_pred))#,target_names=target_names))

              precision    recall  f1-score   support

           0       0.86      0.93      0.89      3846
           1       0.99      0.98      0.99     36051

    accuracy                           0.98     39897
   macro avg       0.92      0.96      0.94     39897
weighted avg       0.98      0.98      0.98     39897



In [129]:
from sklearn.ensemble import AdaBoostClassifier
model_ad = AdaBoostClassifier()
model_ad.fit(x_train_res , y_train_res)
y_pred = model_GB.predict(val_x)
target_names = ['Accept', 'Not_Accept']
print(classification_report(val_y, y_pred))#,target_names=target_names))

              precision    recall  f1-score   support

           0       0.86      0.93      0.89      3846
           1       0.99      0.98      0.99     36051

    accuracy                           0.98     39897
   macro avg       0.92      0.96      0.94     39897
weighted avg       0.98      0.98      0.98     39897



In [130]:
#Apply Random Forest or any other model to predict the probability of "participant_status" i.e. 0 or 1 for different drivers given the same 
#order_id and then return the driver with the maximum probability of accepting the request

In [131]:
# def convert_pred_to_0_1(group):
#     df = pd.DataFrame(group)
#     df.iloc[0]["Pred_y"]=1
#     df.iloc[1:]["Pred_y"]=0
#     return df

In [132]:
# transformed_train_data["participant_status"].value_counts()

In [133]:
# transformed_val_data.shape,transformed_train_data.shape

In [134]:
# clf = LogisticRegression(random_state=0).fit(train_x, train_y)
# val_pred_y = clf.predict(val_x)
# val_pred_y_df = pd.DataFrame(val_pred_y,columns=["Pred_y"])
# transformed_val_data["index"]=transformed_val_data.index
# val_pred_y_df["index"]=val_pred_y_df.index
# x = pd.merge(transformed_val_data,val_pred_y_df,on="index").drop_duplicates()
# result1 = x.sort_values("Pred_y",ascending=False).groupby(["order_id"]).apply(convert_pred_to_0_1)
# score_accuracy =accuracy_score(result1["participant_status"],result1["Pred_y"])
# # metrics = {}
# # metrics["f_score_class_1"]=f1_score(result1["participant_status"],result1["Pred_y"],pos_label=1)
# # metrics["f_score_class_0"]=f1_score(result1["participant_status"],result1["Pred_y"],pos_label=0)

In [135]:
# print(score_accuracy)

In [136]:
# #This is calculated to see that I should not assign a ride to a wrong driver or a driver that is highly probable to cancel. Looking
# #at the results we see that for 291/3984 rides, I assigned a wrong driver. While 15/3984 drivers I predicted as the ones who won't 
# #accept the ride despite the fact that they actually did
# result1=pd.DataFrame(result1)
# print(result1.shape)
# result1.loc[(result1["Pred_y"]==1.0) & (result1["participant_status"]==0.0)]

In [137]:
# def is_correct_driver_identified(x):
#     x = pd.DataFrame(x)
#     x["is_correct_driver_identified"] = 0
#     for i in range(x.shape[0]):
#         if ((x.iloc[i]["participant_status"] == 1.0) and (x.iloc[i]["Pred_y"] == 1.0)):
#             x["is_correct_driver_identified"] = 1
#     return x

In [138]:
# import sklearn
# clf = LogisticRegression(random_state=0).fit(train_x, train_y)
# print(sklearn.metrics.roc_auc_score(train_y, clf.predict_proba(train_x)[:, 1]))
# print(sklearn.metrics.roc_auc_score(val_y, clf.predict_proba(val_x)[:, 1]))

In [139]:
# result1 = result1.groupby(["order_id"]).apply(lambda x: is_correct_driver_identified(x))

In [140]:
# #Recall (i.e. 92% of the time I was able to capture the right driver). Note that our model is giving 1 only to 1 driver that has got the maximum prediction probability and rest all drivers get 0 
# #while in practise for the same order ID multiple drivers have 1. This leads to an illusion that I missed potential drivers.
# result1["is_correct_driver_identified"].mean()

In [141]:
# result1.sort_values("order_id")

In [142]:
# result1.loc[(result1["order_id"]==526935910500)]

In [143]:
# result1.sort_values("order_id")

In [144]:
# transformed_test_data_x = transformed_test_data.drop(["order_id","customer_id"],axis=1)
# test_pred_y = clf.predict(transformed_test_data_x)
# test_pred_y_df = pd.DataFrame(test_pred_y,columns=["Pred_y"])
# test_pred_y_df["index"]=test_pred_y_df.index
# transformed_test_data["index"] = transformed_test_data.index
# x = pd.merge(transformed_test_data,test_pred_y_df,on="index").drop_duplicates()
# result2 = pd.DataFrame(x.sort_values("Pred_y",ascending=False).groupby('order_id').first().reset_index())
# result2 = result2[["order_id","driver_id"]]

In [145]:
# result2.to_csv("results_mahima.csv")

Random forest shall work better than LR or SVM as it can not only learn non linear relationship like SVM but is also faster and deals better with large data.  

In [146]:
# # param_grid = { 
# #     'n_estimators': [200, 500],
# #     'max_features': ['auto', 'sqrt', 'log2'],
# #     'max_depth' : [4,8,16,32],
# #     'criterion' :['entropy','gini'],
# # }

# rf_estimator = RandomForestClassifier(n_jobs=-1,random_state=33,bootstrap=False,class_weight="balanced",n_estimators=200)
# # CV_rfc = GridSearchCV(estimator=rf_estimator, param_grid=param_grid, cv= 4)
# # CV_rfc.fit(train_x,train_y)
# # CV_rfc.best_params_
# rf_estimator.fit(train_x,train_y)

In [147]:
# #dict(zip(features, CV_rfc.best_estimator_.feature_importances_))     
# y_true=val_y.values
# #y_pred=CV_rfc.best_estimator_.predict(val_x.values,type = 'prob')
# y_pred=rf_estimator.predict(val_x.values)

In [148]:
# val_pred_y_df = pd.DataFrame(val_pred_y,columns=["Pred_y"])
# transformed_val_data["index"]=transformed_val_data.index
# val_pred_y_df["index"]=val_pred_y_df.index
# x = pd.merge(transformed_val_data,val_pred_y_df,on="index").drop_duplicates()
# result1 = x.sort_values("Pred_y",ascending=False).groupby(["order_id"]).apply(convert_pred_to_0_1)
# score_accuracy =accuracy_score(result1["participant_status"],result1["Pred_y"])
# print("score_accuracy:",score_accuracy)
# result1=pd.DataFrame(result1)
# print(result1.shape)
# result1.loc[(result1["Pred_y"]==1.0) & (result1["participant_status"]==0.0)]
# result1 = result1.groupby(["order_id"]).apply(lambda x: is_correct_driver_identified(x))
# print("Recall:",result1["is_correct_driver_identified"].mean())

In [149]:
# y_pred

In [150]:
# metrics = {}
# metrics["f_score_class_1"]=f1_score(y_true,y_pred,pos_label=1)
# metrics["f_score_class_0"]=f1_score(y_true,y_pred,pos_label=0)
# metrics

In [151]:
# import sklearn
# print(sklearn.metrics.roc_auc_score(train_y, clf.predict_proba(train_x)[:, 1]))
# print(sklearn.metrics.roc_auc_score(val_y, clf.predict_proba(val_x)[:, 1]))